In [1]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
from sklearn.cluster import KMeans
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import accuracy_score, f1_score, recall_score
from sklearn.feature_selection import mutual_info_classif

In [2]:
train = pd.read_csv('Data Mining VU data/training_set_VU_DM_2014.csv')
test = pd.read_csv('Data Mining VU data/test_set_VU_DM_2014.csv')

In [3]:
train_clean = pd.read_csv('processed_data/train_clean.csv')
test_clean = pd.read_csv('processed_data/test_clean.csv')

In [4]:
srch_id_groups = train_clean.groupby('srch_id')
all_srch_ids = train_clean.srch_id.unique()
num_samples = int(0.1*len(all_srch_ids))
train_sample_ids = np.random.choice(all_srch_ids, num_samples, replace=False)
remaining_ids = list(set(all_srch_ids)-set(train_sample_ids))
test_sample_ids = np.random.choice(remaining_ids, num_samples, replace=False)

train_sample = pd.concat([srch_id_groups.get_group(group) for group in train_sample_ids])
test_sample = pd.concat([srch_id_groups.get_group(group) for group in test_sample_ids])


In [11]:
def fit_model(model, training_set, features, target):
    return model.fit(training_set[features], training_set[target])

def predict(model, test_set, features):
    test_set['probability'] = model.predict_proba(test_set[features])[:,1]
    ranking_list = []
    srch_id_list = []
    num_ids = len(test_set.srch_id.unique())
    current = 1
    for i in test_set.srch_id.unique():
        ranking = test_set[test_set.srch_id==i]
        srch_id_list.extend(ranking.srch_id.values)
        ranking = ranking.as_matrix(columns=['srch_id','prop_id','probability'])
        ranking = np.flipud(ranking[ranking[:,2].argsort(kind='mergesort')])
        ranking_list = np.concatenate((ranking_list,ranking[:,1]))
        print('{} out of {} srch_ids done'.format(current, num_ids))
        current += 1
    test_set.drop('probability', axis=1, inplace=True)
    return pd.DataFrame(np.array([srch_id_list, ranking_list]).T, columns=['srch_id','prop_id'])

In [15]:
def ideal_ranking(ground_truth):
    ideal_ranking = ground_truth.sort_values(by=['booking_bool', 'click_bool'], ascending=False)
    return ideal_ranking.reset_index(drop=True)
    
def DCG(prediction, ground_truth):
    dcg = []
    for row in prediction.itertuples():
        prop_id = getattr(row, 'prop_id')
        rank = getattr(row, 'Index') + 1
        booked = ground_truth.set_index('prop_id').loc[prop_id,'booking_bool']
        clicked = ground_truth.set_index('prop_id').loc[prop_id,'click_bool']
        score = 5 if booked else 1 if clicked else 0
        dcg.append((2**score - 1)/(np.log2(rank + 1)))
    return sum(dcg)

def nDCG(prediction, ground_truth):
    prediction.reset_index(drop=True, inplace=True)
    dcg = DCG(prediction, ground_truth)
    idcg = DCG(ideal_ranking(ground_truth), ground_truth)
    return(dcg/idcg)

def overall_nDCG(prediction, ground_truth):
    ids = prediction.srch_id.unique()
    srch_id_groups_pred = prediction.groupby('srch_id')
    srch_id_groups_gt = ground_truth.groupby('srch_id')
    all_nDCG = [nDCG(srch_id_groups_pred.get_group(i), srch_id_groups_gt.get_group(i)) for i in ids]
    #print(all_nDCG)
    print(np.mean(all_nDCG))

# predict booking_bool

In [16]:
diff_cols = [[c for c in train_clean.columns if c not in ['position', 'date_time', 'visitor_hist_starrating', 'visitor_hist_adr_usd', 'gross_bookings_usd', 'star_diff', 'price_diff', 'booking_bool', 'click_bool', 'booked_clicked_combined']], ['prop_desirability', 'price_usd', 'prop_location_score2', 'prop_location_score1'], ['price_diff_filled', 'srch_booking_window', 'orig_destination_distance'], ['prop_desirability', 'srch_id'], ['prop_desirability', 'orig_destination_distance', 'price_usd'], ['srch_id', 'orig_destination_distance', 'price_usd', 'willingness_to_pay'], ['srch_booking_window', 'orig_destination_distance', 'prop_desirability'], ['srch_booking_window', 'orig_destination_distance', 'price_usd', 'prop_location_score2', 'prop_desirability'], ['srch_booking_window', 'orig_destination_distance', 'price_usd', 'prop_location_score2', 'prop_desirability', 'star_diff_filled'], ['srch_booking_window', 'orig_destination_distance', 'price_usd', 'prop_location_score2', 'prop_desirability', 'star_diff_filled', 'srch_id']]

for i in range(len(diff_cols)):
    col = diff_cols[i]
    
    rf_model = fit_model(RandomForestClassifier(), train_sample, col, 'booking_bool')
    rf_prediction = predict(rf_model, test_sample, col)
    
    print(i)
    overall_nDCG(rf_prediction, test_sample)


1 out of 19979 srch_ids done
2 out of 19979 srch_ids done
3 out of 19979 srch_ids done
4 out of 19979 srch_ids done
5 out of 19979 srch_ids done
6 out of 19979 srch_ids done
7 out of 19979 srch_ids done
8 out of 19979 srch_ids done
9 out of 19979 srch_ids done
10 out of 19979 srch_ids done
11 out of 19979 srch_ids done
12 out of 19979 srch_ids done
13 out of 19979 srch_ids done
14 out of 19979 srch_ids done
15 out of 19979 srch_ids done
16 out of 19979 srch_ids done
17 out of 19979 srch_ids done
18 out of 19979 srch_ids done
19 out of 19979 srch_ids done
20 out of 19979 srch_ids done
21 out of 19979 srch_ids done
22 out of 19979 srch_ids done
23 out of 19979 srch_ids done
24 out of 19979 srch_ids done
25 out of 19979 srch_ids done
26 out of 19979 srch_ids done
27 out of 19979 srch_ids done
28 out of 19979 srch_ids done
29 out of 19979 srch_ids done
30 out of 19979 srch_ids done
31 out of 19979 srch_ids done
32 out of 19979 srch_ids done
33 out of 19979 srch_ids done
34 out of 19979 src

292 out of 19979 srch_ids done
293 out of 19979 srch_ids done
294 out of 19979 srch_ids done
295 out of 19979 srch_ids done
296 out of 19979 srch_ids done
297 out of 19979 srch_ids done
298 out of 19979 srch_ids done
299 out of 19979 srch_ids done
300 out of 19979 srch_ids done
301 out of 19979 srch_ids done
302 out of 19979 srch_ids done
303 out of 19979 srch_ids done
304 out of 19979 srch_ids done
305 out of 19979 srch_ids done
306 out of 19979 srch_ids done
307 out of 19979 srch_ids done
308 out of 19979 srch_ids done
309 out of 19979 srch_ids done
310 out of 19979 srch_ids done
311 out of 19979 srch_ids done
312 out of 19979 srch_ids done
313 out of 19979 srch_ids done
314 out of 19979 srch_ids done
315 out of 19979 srch_ids done
316 out of 19979 srch_ids done
317 out of 19979 srch_ids done
318 out of 19979 srch_ids done
319 out of 19979 srch_ids done
320 out of 19979 srch_ids done
321 out of 19979 srch_ids done
322 out of 19979 srch_ids done
323 out of 19979 srch_ids done
324 out 

612 out of 19979 srch_ids done
613 out of 19979 srch_ids done
614 out of 19979 srch_ids done
615 out of 19979 srch_ids done
616 out of 19979 srch_ids done
617 out of 19979 srch_ids done
618 out of 19979 srch_ids done
619 out of 19979 srch_ids done
620 out of 19979 srch_ids done
621 out of 19979 srch_ids done
622 out of 19979 srch_ids done
623 out of 19979 srch_ids done
624 out of 19979 srch_ids done
625 out of 19979 srch_ids done
626 out of 19979 srch_ids done
627 out of 19979 srch_ids done
628 out of 19979 srch_ids done
629 out of 19979 srch_ids done
630 out of 19979 srch_ids done
631 out of 19979 srch_ids done
632 out of 19979 srch_ids done
633 out of 19979 srch_ids done
634 out of 19979 srch_ids done
635 out of 19979 srch_ids done
636 out of 19979 srch_ids done
637 out of 19979 srch_ids done
638 out of 19979 srch_ids done
639 out of 19979 srch_ids done
640 out of 19979 srch_ids done
641 out of 19979 srch_ids done
642 out of 19979 srch_ids done
643 out of 19979 srch_ids done
644 out 

905 out of 19979 srch_ids done
906 out of 19979 srch_ids done
907 out of 19979 srch_ids done
908 out of 19979 srch_ids done
909 out of 19979 srch_ids done
910 out of 19979 srch_ids done
911 out of 19979 srch_ids done
912 out of 19979 srch_ids done
913 out of 19979 srch_ids done
914 out of 19979 srch_ids done
915 out of 19979 srch_ids done
916 out of 19979 srch_ids done
917 out of 19979 srch_ids done
918 out of 19979 srch_ids done
919 out of 19979 srch_ids done
920 out of 19979 srch_ids done
921 out of 19979 srch_ids done
922 out of 19979 srch_ids done
923 out of 19979 srch_ids done
924 out of 19979 srch_ids done
925 out of 19979 srch_ids done
926 out of 19979 srch_ids done
927 out of 19979 srch_ids done
928 out of 19979 srch_ids done
929 out of 19979 srch_ids done
930 out of 19979 srch_ids done
931 out of 19979 srch_ids done
932 out of 19979 srch_ids done
933 out of 19979 srch_ids done
934 out of 19979 srch_ids done
935 out of 19979 srch_ids done
936 out of 19979 srch_ids done
937 out 

1227 out of 19979 srch_ids done
1228 out of 19979 srch_ids done
1229 out of 19979 srch_ids done
1230 out of 19979 srch_ids done
1231 out of 19979 srch_ids done
1232 out of 19979 srch_ids done
1233 out of 19979 srch_ids done
1234 out of 19979 srch_ids done
1235 out of 19979 srch_ids done
1236 out of 19979 srch_ids done
1237 out of 19979 srch_ids done
1238 out of 19979 srch_ids done
1239 out of 19979 srch_ids done
1240 out of 19979 srch_ids done
1241 out of 19979 srch_ids done
1242 out of 19979 srch_ids done
1243 out of 19979 srch_ids done
1244 out of 19979 srch_ids done
1245 out of 19979 srch_ids done
1246 out of 19979 srch_ids done
1247 out of 19979 srch_ids done
1248 out of 19979 srch_ids done
1249 out of 19979 srch_ids done
1250 out of 19979 srch_ids done
1251 out of 19979 srch_ids done
1252 out of 19979 srch_ids done
1253 out of 19979 srch_ids done
1254 out of 19979 srch_ids done
1255 out of 19979 srch_ids done
1256 out of 19979 srch_ids done
1257 out of 19979 srch_ids done
1258 out

...

19127 out of 19979 srch_ids done
19128 out of 19979 srch_ids done
19129 out of 19979 srch_ids done
19130 out of 19979 srch_ids done
19131 out of 19979 srch_ids done
19132 out of 19979 srch_ids done
19133 out of 19979 srch_ids done
19134 out of 19979 srch_ids done
19135 out of 19979 srch_ids done
19136 out of 19979 srch_ids done
19137 out of 19979 srch_ids done
19138 out of 19979 srch_ids done
19139 out of 19979 srch_ids done
19140 out of 19979 srch_ids done
19141 out of 19979 srch_ids done
19142 out of 19979 srch_ids done
19143 out of 19979 srch_ids done
19144 out of 19979 srch_ids done
19145 out of 19979 srch_ids done
19146 out of 19979 srch_ids done
19147 out of 19979 srch_ids done
19148 out of 19979 srch_ids done
19149 out of 19979 srch_ids done
19150 out of 19979 srch_ids done
19151 out of 19979 srch_ids done
19152 out of 19979 srch_ids done
19153 out of 19979 srch_ids done
19154 out of 19979 srch_ids done
19155 out of 19979 srch_ids done
19156 out of 19979 srch_ids done
19157 out 

19410 out of 19979 srch_ids done
19411 out of 19979 srch_ids done
19412 out of 19979 srch_ids done
19413 out of 19979 srch_ids done
19414 out of 19979 srch_ids done
19415 out of 19979 srch_ids done
19416 out of 19979 srch_ids done
19417 out of 19979 srch_ids done
19418 out of 19979 srch_ids done
19419 out of 19979 srch_ids done
19420 out of 19979 srch_ids done
19421 out of 19979 srch_ids done
19422 out of 19979 srch_ids done
19423 out of 19979 srch_ids done
19424 out of 19979 srch_ids done
19425 out of 19979 srch_ids done
19426 out of 19979 srch_ids done
19427 out of 19979 srch_ids done
19428 out of 19979 srch_ids done
19429 out of 19979 srch_ids done
19430 out of 19979 srch_ids done
19431 out of 19979 srch_ids done
19432 out of 19979 srch_ids done
19433 out of 19979 srch_ids done
19434 out of 19979 srch_ids done
19435 out of 19979 srch_ids done
19436 out of 19979 srch_ids done
19437 out of 19979 srch_ids done
19438 out of 19979 srch_ids done
19439 out of 19979 srch_ids done
19440 out 

19700 out of 19979 srch_ids done
19701 out of 19979 srch_ids done
19702 out of 19979 srch_ids done
19703 out of 19979 srch_ids done
19704 out of 19979 srch_ids done
19705 out of 19979 srch_ids done
19706 out of 19979 srch_ids done
19707 out of 19979 srch_ids done
19708 out of 19979 srch_ids done
19709 out of 19979 srch_ids done
19710 out of 19979 srch_ids done
19711 out of 19979 srch_ids done
19712 out of 19979 srch_ids done
19713 out of 19979 srch_ids done
19714 out of 19979 srch_ids done
19715 out of 19979 srch_ids done
19716 out of 19979 srch_ids done
19717 out of 19979 srch_ids done
19718 out of 19979 srch_ids done
19719 out of 19979 srch_ids done
19720 out of 19979 srch_ids done
19721 out of 19979 srch_ids done
19722 out of 19979 srch_ids done
19723 out of 19979 srch_ids done
19724 out of 19979 srch_ids done
19725 out of 19979 srch_ids done
19726 out of 19979 srch_ids done
19727 out of 19979 srch_ids done
19728 out of 19979 srch_ids done
19729 out of 19979 srch_ids done
19730 out 

19979 out of 19979 srch_ids done
4


KeyboardInterrupt: 